In [1]:
import pandas as pd
import folium
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
df = pd.read_csv('./Cleaned_2018_Flights.csv')
df.head(5)

ID       ItinID          MktID  MktCoupons  Quarter Origin  OriginWac Dest  \
0   0  20181767585  2018176758501           1        1    PHL         23  LAX   
1   1  20181767586  2018176758601           1        1    PHL         23  LAX   
2   2  20181767587  2018176758701           1        1    PHL         23  LAX   
3   3  20181767636  2018176763601           1        1    PHL         23  LAX   
4   4  20181767637  2018176763701           1        1    PHL         23  LAX   

   DestWac   Miles  ContiguousUSA  NumTicketsOrdered AirlineCompany  \
0       91  2402.0              2                1.0             AA   
1       91  2402.0              2                1.0             AA   
2       91  2402.0              2                1.0             AA   
3       91  2402.0              2                1.0             AA   
4       91  2402.0              2                1.0             AA   

   PricePerTicket  
0          672.87  
1          367.68  
2          417.94  
3          247.10  
4          276.35

In [3]:
a= df.groupby(['Origin','Dest']).count()
a.reset_index(inplace=True)
a=a[['Origin','Dest','ID']]
a['Origin'] = a['Origin'].map({'DFW':'MEX',
                 'JFK':'CUN',
                 'PHX':'GDL',
                 'FLL':'MTY',
                 'MSP':'TIJ',
                 'DTW':'SJD',
                 'SAN':'PVR',
                 'TPA':'MID',
                 'LGA':'BJX',
                 'BWI':'CUL'
                }).fillna(a['Origin'])
a['Dest'] = a['Dest'].map({'DFW':'MEX',
                 'JFK':'CUN',
                 'PHX':'GDL',
                 'FLL':'MTY',
                 'MSP':'TIJ',
                 'DTW':'SJD',
                 'SAN':'PVR',
                 'TPA':'MID',
                 'LGA':'BJX',
                 'BWI':'CUL'
                }).fillna(a['Dest'])
a.head(5)

Origin Dest   ID
0    ABE  ATL  414
1    ABE  MTY  321
2    ABE  MYR  281
3    ABE  ORD    5
4    ABE  PGD  830

In [2]:
ac = pd.read_csv('./airports-extended.csv')
ac.head(5)

ID                                         name        region  \
0   1                               Goroka Airport        Goroka   
1   2                               Madang Airport        Madang   
2   3                 Mount Hagen Kagamuga Airport   Mount Hagen   
3   4                               Nadzab Airport        Nadzab   
4   5  Port Moresby Jacksons International Airport  Port Moresby   

            country code3 code4       lat        long  altitude timezone UTC  \
0  Papua New Guinea   GKA  AYGA -6.081690  145.391998      5282       10   U   
1  Papua New Guinea   MAG  AYMD -5.207080  145.789001        20       10   U   
2  Papua New Guinea   HGU  AYMH -5.826790  144.296005      5388       10   U   
3  Papua New Guinea   LAE  AYNZ -6.569803  146.725977       239       10   U   
4  Papua New Guinea   POM  AYPY -9.443380  147.220001       146       10   U   

                     TZ     type       source  
0  Pacific/Port_Moresby  airport  OurAirports  
1  Pacific/Port_Moresby  airport  OurAirports  
2  Pacific/Port_Moresby  airport  OurAirports  
3  Pacific/Port_Moresby  airport  OurAirports  
4  Pacific/Port_Moresby  airport  OurAirports

In [6]:
ac['type'].unique()

array(['airport', 'unknown', 'station', 'port'], dtype=object)

In [5]:
a = a.merge(ac[['code3','lat', 'long']], left_on='Origin', right_on='code3').rename(columns={'lat':'lat_origin','long':'long_origin'})
a = a.merge(ac[['code3','lat', 'long']], left_on='Dest', right_on='code3').rename(columns={'lat':'lat_dest','long':'long_dest'})
a = a[['Origin', 'Dest', 'ID', 'lat_origin', 'long_origin', 'lat_dest', 'long_dest']]
b= a.rename(columns={'ID':'count'})
b

Origin Dest  count  lat_origin  long_origin   lat_dest   long_dest
0       ABE  ATL    414   40.652100   -75.440804  33.636700  -84.428101
1       ABQ  ATL   1528   35.040199  -106.609001  33.636700  -84.428101
2       ACY  ATL    264   39.457600   -74.577202  33.636700  -84.428101
3       AGS  ATL     51   33.369900   -81.964500  33.636700  -84.428101
4       ALB  ATL   1778   42.748299   -73.801697  33.636700  -84.428101
...     ...  ...    ...         ...          ...        ...         ...
8454    PIE  YNG      7   27.910200   -82.687401  41.260700  -80.679100
8455    SFB  YNG      2   28.777599   -81.237503  41.260700  -80.679100
8456    SFB  OWB    401   28.777599   -81.237503  37.740101  -87.166801
8457    SFO  OTH      5   37.618999  -122.375000  43.417099 -124.246002
8458    SFO  RDM      2   37.618999  -122.375000  44.254101 -121.150002

[8459 rows x 7 columns]

In [6]:
start_location_lat = ac[ac['country']=='United States']['lat'].median()
start_location_long = ac[ac['country']=='United States']['long'].median()

In [7]:
m = folium.Map(location =[start_location_lat, start_location_long], zoom_start=4)

for row in ac[((ac['country']=='United States') )& (ac['code3'].isin(b['Origin']))].itertuples():
    folium.Marker([row.lat,row.long] , tooltip = row.name, icon = folium.Icon(color='blue')).add_to(m)
for row in ac[((ac['country']=='Mexico') )& (ac['code3'].isin(b['Origin']))].itertuples():
    folium.Marker([row.lat,row.long] , tooltip = row.name, icon=folium.Icon(color='green')).add_to(m)

for row in b.itertuples():
    folium.PolyLine([[row.lat_origin,row.long_origin],[row.lat_dest,row.long_dest]], weight =(row.count)/3000, opacity=0.2).add_to(m)

m